# Lecture 8

## Linear shape functions for a triangle

In [5]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# =========================================================
# Appearance settings
# =========================================================
GRID_COLOR   = "rgba(0,0,0,0.35)"   # wireframe grid lines on the surfaces
LINE_WIDTH   = 1.2
BASE_COLOR   = "#bbbbbb"            # base polygon fill (distinct from grid)
BASE_OPACITY = 0.50                 # more solid base (was 0.65)

# Shared color palette for shape functions
COLORS = {
    "N1": "#d62728",  # red
    "N2": "#1f77b4",  # blue
    "N3": "#ff7f0e",  # orange
    "N4": "#2ca02c",  # green
}

# =========================================================
# Helper: Constant-color Surface with structured wireframe
# =========================================================
def const_color_surface(x, y, z, color, name,
                        show_grid=True,
                        step_x=None, step_y=None,
                        line_color=GRID_COLOR, line_width=LINE_WIDTH):
    sc = np.ones_like(z)  # constant color
    trace = go.Surface(
        x=x, y=y, z=z, surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False, opacity=1.0, name=name,
        # Hover: z-only (no x/y shown)
        hovertemplate="N=%{z:.3f}<extra></extra>"
    )
    if show_grid:
        xmin, xmax = np.nanmin(x), np.nanmax(x)
        ymin, ymax = np.nanmin(y), np.nanmax(y)
        # Defaults if not provided
        if step_x is None: step_x = max(0.20, (xmax - xmin) / 5.0)
        if step_y is None: step_y = max(0.20, (ymax - ymin) / 5.0)
        # Structured wireframe: x/y only
        trace.update(contours=dict(
            x=dict(show=True, color=line_color, width=line_width,
                   start=xmin, end=xmax, size=step_x),
            y=dict(show=True, color=line_color, width=line_width,
                   start=ymin, end=ymax, size=step_y),
            z=dict(show=False)  # no horizontal iso-lines
        ))
    trace.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2),
                 lightposition=dict(x=100, y=200, z=300))
    return trace

# =========================================================
# TRIANGLE (CST) — 3×1 grid
# =========================================================
n = 121
x = np.linspace(0, 1, n)
y = np.linspace(0, 1, n)
X, Y = np.meshgrid(x, y)

# Mask outside the reference triangle
mask = (X + Y) <= 1
def masked(Z): return np.where(mask, Z, np.nan)

# Linear triangle shape functions
N1_tri = 1 - X - Y
N2_tri = X
N3_tri = Y

fig_tri = make_subplots(
    rows=1, cols=3,
    specs=[[{"type": "scene"}, {"type": "scene"}, {"type": "scene"}]],
    horizontal_spacing=0.02, vertical_spacing=0.02,
    subplot_titles=("N1", "N2", "N3")
)

# Triangle base outline & nodes (reference domain)
base_triangle_x = [0, 1, 0, 0]
base_triangle_y = [0, 0, 1, 0]
base_triangle_z = [0, 0, 0, 0]
triangle_nodes_x = [0, 1, 0]
triangle_nodes_y = [0, 0, 1]
triangle_nodes_z = [0, 0, 0]

# Triangle base filled polygon (Mesh3d at z=0)
base_tri_mesh = go.Mesh3d(
    x=[0, 1, 0], y=[0, 0, 1], z=[0, 0, 0],
    i=[0], j=[1], k=[2],
    color=BASE_COLOR, opacity=BASE_OPACITY,
    flatshading=True, showscale=False,
    name="Triangle base",
    hoverinfo="skip"  # no hover on base
)

for i_sub, (Z, name, col) in enumerate([(masked(N1_tri),"N1",COLORS["N1"]),
                                        (masked(N2_tri),"N2",COLORS["N2"]),
                                        (masked(N3_tri),"N3",COLORS["N3"])], start=1):
    # Surface with structured wireframe; hover shows z only
    fig_tri.add_trace(
        const_color_surface(X, Y, Z, col, name,
                            step_x=0.20, step_y=0.20),
        row=1, col=i_sub
    )
    # Base filled polygon (mesh) – add a separate copy per subplot
    fig_tri.add_trace(base_tri_mesh, row=1, col=i_sub)
    # Base outline (black)
    fig_tri.add_trace(go.Scatter3d(
        x=base_triangle_x, y=base_triangle_y, z=base_triangle_z,
        mode="lines",
        line=dict(color="black", width=6),
        showlegend=False,
        hoverinfo="skip"
    ), row=1, col=i_sub)
    # Node markers (black)
    fig_tri.add_trace(go.Scatter3d(
        x=triangle_nodes_x, y=triangle_nodes_y, z=triangle_nodes_z,
        mode="markers",
        marker=dict(size=6, color="black"),
        showlegend=False,
        hoverinfo="skip"
    ), row=1, col=i_sub)

fig_tri.update_layout(
    title="Linear (CST) Triangle Shape Functions",
    width=1400, height=420,
    margin=dict(l=20, r=20, t=60, b=20)
)
for s in ["scene","scene2","scene3"]:
    fig_tri.update_layout(**{s: dict(xaxis=dict(range=[0,1]),
                                     yaxis=dict(range=[0,1]),
                                     zaxis=dict(range=[0,1]))})
fig_tri.update_scenes(xaxis_title="x", yaxis_title="y", zaxis_title="N(x,y)", aspectmode="cube")
fig_tri.show()

# =========================================================
# QUAD (Q4/Melosh) — 2×2 grid
# =========================================================
m = 121
zeta = np.linspace(-1, 1, m)
eta  = np.linspace(-1, 1, m)
ZZ, EE = np.meshgrid(zeta, eta)

N1_rec = 0.25 * (1 - ZZ) * (1 - EE)
N2_rec = 0.25 * (1 + ZZ) * (1 - EE)
N3_rec = 0.25 * (1 + ZZ) * (1 + EE)
N4_rec = 0.25 * (1 - ZZ) * (1 + EE)

fig_rec = make_subplots(
    rows=2, cols=2,
    specs=[[{"type":"scene"},{"type":"scene"}],[{"type":"scene"},{"type":"scene"}]],
    horizontal_spacing=0.03, vertical_spacing=0.03,
    subplot_titles=("N1", "N2", "N3", "N4")
)

# Rectangle base outline & nodes (reference domain)
base_rect_x = [-1, 1, 1, -1, -1]
base_rect_y = [-1, -1, 1, 1, -1]
base_rect_z = [0, 0, 0, 0, 0]
rect_nodes_x = [-1, 1, 1, -1]
rect_nodes_y = [-1, -1, 1, 1]
rect_nodes_z = [0, 0, 0, 0]

# Rectangle base filled polygon (Mesh3d at z=0) – two triangles
base_rect_mesh = go.Mesh3d(
    x=[-1, 1, 1, -1], y=[-1, -1, 1, 1], z=[0, 0, 0, 0],
    i=[0, 0], j=[1, 2], k=[2, 3],  # faces: (0,1,2) and (0,2,3)
    color=BASE_COLOR, opacity=BASE_OPACITY,
    flatshading=True, showscale=False,
    name="Rectangle base",
    hoverinfo="skip"
)

surfs = [(N1_rec,"N1",COLORS["N1"]), (N2_rec,"N2",COLORS["N2"]),
         (N3_rec,"N3",COLORS["N3"]), (N4_rec,"N4",COLORS["N4"])]
r_c = [(1,1),(1,2),(2,1),(2,2)]
for (Z,name,col),(r,c) in zip(surfs,r_c):
    # Surface with structured wireframe; hover shows z only
    fig_rec.add_trace(
        const_color_surface(ZZ, EE, Z, col, name,
                            step_x=0.50, step_y=0.50),
        row=r, col=c
    )
    # Base filled polygon (mesh)
    fig_rec.add_trace(base_rect_mesh, row=r, col=c)
    # Base outline (black)
    fig_rec.add_trace(go.Scatter3d(
        x=base_rect_x, y=base_rect_y, z=base_rect_z,
        mode="lines",
        line=dict(color="black", width=6),
        showlegend=False,
        hoverinfo="skip"
    ), row=r, col=c)
    # Node markers (black)
    fig_rec.add_trace(go.Scatter3d(
        x=rect_nodes_x, y=rect_nodes_y, z=rect_nodes_z,
        mode="markers",
        marker=dict(size=6, color="black"),
        showlegend=False,
        hoverinfo="skip"
    ), row=r, col=c)

# fig_rec.update_layout(
#     title="Bilinear (Q4/Melosh) Shape Functions (plotted for x, y ∈ [-1, 1])",
#     width=950, height=950,
#     margin=dict(l=20, r=20, t=60, b=20)
# )
# for s in ["scene","scene2","scene3","scene4"]:
#     fig_rec.update_layout(**{s: dict(xaxis=dict(range=[-1,1]),
#                                      yaxis=dict(range=[-1,1]),
#                                      zaxis=dict(range=[0,1]))})
# fig_rec.update_scenes(xaxis_title="ζ", yaxis_title="η", zaxis_title="N(ζ,η)", aspectmode="cube")
# fig_rec.show()

## All shape functions overlayed
Illustrates that on each edge only two shape functions are nonzero 

In [6]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# =========================================================
# Common helpers
# =========================================================

# Constant color surface factory (no colorbar, constant color)
def const_color_surface(x, y, z, color, name, show_grid=True):
    sc = np.ones_like(z)  # constant surfacecolor array
    trace = go.Surface(
        x=x, y=y, z=z, surfacecolor=sc,
        colorscale=[[0, color], [1, color]],
        showscale=False, opacity=0.9, name=name
    )
    if show_grid:
        # Add contour lines on x/y/z to create a "grid" feel on the surface
        trace.update(
            contours = dict(
                x=dict(show=True, color="rgba(0,0,0,0.35)", width=1.0, start=np.nanmin(x), end=np.nanmax(x), size=(x[0,1]-x[0,0]) if x.ndim==2 else 0.05),
                y=dict(show=True, color="rgba(0,0,0,0.35)", width=1.0, start=np.nanmin(y), end=np.nanmax(y), size=(y[1,0]-y[0,0]) if y.ndim==2 else 0.05),
                z=dict(show=True, color="rgba(0,0,0,0.25)", width=1.0, start=0.0, end=1.0, size=0.1)
            )
        )
    # Subtle lighting for more depth
    trace.update(lighting=dict(ambient=0.6, diffuse=0.6, specular=0.2), lightposition=dict(x=100, y=200, z=300))
    return trace

# Shared color palette (use the same across triangle and quad)
COLORS = {
    "N1": "#d62728",  # red
    "N2": "#1f77b4",  # blue
    "N3": "#ff7f0e",  # orange
    "N4": "#2ca02c",  # green
}

# =========================================================
# TRIANGLE (CST) — domain & shape functions
# =========================================================
n = 121
x = np.linspace(0, 1, n)
y = np.linspace(0, 1, n)
X, Y = np.meshgrid(x, y)

# Mask outside the reference triangle (x>=0, y>=0, x+y<=1)
mask = (X + Y) <= 1
def masked(Z):
    Zm = np.where(mask, Z, np.nan)
    return Zm

N1_tri = 1 - X - Y
N2_tri = X
N3_tri = Y

# =========================================================
# Triangle overlay (all N1–N3 in one scene)
# =========================================================
fig_tri_overlay = go.Figure()
fig_tri_overlay.add_trace(const_color_surface(X, Y, masked(N1_tri), COLORS["N1"], "N1"))
fig_tri_overlay.add_trace(const_color_surface(X, Y, masked(N2_tri), COLORS["N2"], "N2"))
fig_tri_overlay.add_trace(const_color_surface(X, Y, masked(N3_tri), COLORS["N3"], "N3"))
fig_tri_overlay.update_layout(
    title="Linear (CST) Triangle — Overlay of N1, N2, N3",
    width=650, height=520,
    margin=dict(l=20, r=20, t=60, b=20),
    legend=dict(orientation="h")
)
fig_tri_overlay.update_scenes(
    xaxis_title="x", yaxis_title="y", zaxis_title="N(x,y)",
    aspectmode="cube",
    xaxis=dict(range=[0,1]), yaxis=dict(range=[0,1]), zaxis=dict(range=[0,1])
)
fig_tri_overlay.show()


## Global shape functions
When all local shape function connected to a node are drawn they for a global hat function

In [7]:
import numpy as np
import plotly.graph_objects as go

# --- Colors ---
RED   = "#d62728"
EDGE_COLOR = "black"  # contrasting color for element edges
GRID_COLOR = "rgba(0,0,0,0.4)"  # underlying grid lines

# --- Square corners and shared node O ---
A = np.array([0.0, 0.0])
B = np.array([2.0, 0.0])
C = np.array([2.0, 2.0])
D = np.array([0.0, 2.0])
O = np.array([1.0, 1.0])  # shared central node

# Mesh3d for the four triangles around O
Xv = np.array([A[0], B[0], C[0], D[0], O[0]])
Yv = np.array([A[1], B[1], C[1], D[1], O[1]])
Zv = np.array([0.0, 0.0, 0.0, 0.0, 1.0])  # hat: 0 at corners, 1 at center

i = np.array([0, 1, 2, 3])
j = np.array([1, 2, 3, 0])
k = np.array([4, 4, 4, 4])

mesh_tri_hat = go.Mesh3d(
    x=Xv, y=Yv, z=Zv,
    i=i, j=j, k=k,
    color=RED,
    opacity=0.95,
    flatshading=True,
    name="Triangle global hat",
    showscale=False
)

# --- Coarse iso-lines (vertical only): levels 0.25, 0.50, 0.75 ---
def iso_segment(v0, v1, O, c):
    P0 = (1 - c) * v0 + c * O
    P1 = (1 - c) * v1 + c * O
    return np.array([P0[0], P1[0]]), np.array([P0[1], P1[1]]), np.array([c, c])

def make_iso_lines(levels=(0.25, 0.50, 0.75), line_color=GRID_COLOR, width=2):
    lines = []
    triangles = [(A, B, O), (B, C, O), (C, D, O), (D, A, O)]
    for c in levels:
        for v0, v1, Oo in triangles:
            xs, ys, zs = iso_segment(v0, v1, Oo, c)
            lines.append(go.Scatter3d(
                x=xs, y=ys, z=zs,
                mode="lines",
                line=dict(color=line_color, width=width),
                showlegend=False
            ))
    return lines

# --- Element edges (outer square + diagonals to center) ---
edge_lines = []
edges = [(A, B), (B, C), (C, D), (D, A), (A, O), (B, O), (C, O), (D, O)]
for v0, v1 in edges:
    edge_lines.append(go.Scatter3d(
        x=[v0[0], v1[0]], y=[v0[1], v1[1]], z=[0.0 if np.all(v0!=O) else Zv[4], 0.0 if np.all(v1!=O) else Zv[4]],
        mode="lines",
        line=dict(color=EDGE_COLOR, width=5),
        showlegend=False
    ))

fig_hat_tri_mesh = go.Figure([mesh_tri_hat] + make_iso_lines() + edge_lines)
fig_hat_tri_mesh.update_layout(
    title="Global Hat Function for linear triangles (4 triangles meeting at a center point)",
    width=700, height=560,
    margin=dict(l=20, r=20, t=60, b=20),
)
fig_hat_tri_mesh.update_scenes(
    xaxis_title="x", yaxis_title="y", zaxis_title="N(x,y)",
    aspectmode="cube",
    xaxis=dict(range=[0, 2]),
    yaxis=dict(range=[0, 2]),
    zaxis=dict(range=[0, 1])
)
fig_hat_tri_mesh.show()